## Clone Repo

In [ ]:
!cd /content
!rm -rf sample_data ChatTTS
!git clone https://github.com/2noise/ChatTTS.git

## Install Requirements

In [ ]:
!pip install -r /content/ChatTTS/requirements.txt
!ldconfig /usr/lib64-nvidia

## Import Packages

In [6]:
import torch

torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision("high")

from ChatTTS import ChatTTS
from ChatTTS.tools.logger import get_logger
from ChatTTS.tools.normalizer import normalizer_en_nemo_text, normalizer_zh_tn
from IPython.display import Audio

## Load Models

In [7]:
logger = get_logger("ChatTTS", format_root=True)
chat = ChatTTS.Chat(logger)

# try to load normalizer
try:
    chat.normalizer.register("en", normalizer_en_nemo_text())
except ValueError as e:
    logger.error(e)
except:
    logger.warning("Package nemo_text_processing not found!")
    logger.warning(
        "Run: conda install -c conda-forge pynini=2.1.5 && pip install nemo_text_processing",
    )
try:
    chat.normalizer.register("zh", normalizer_zh_tn())
except ValueError as e:
    logger.error(e)
except:
    logger.warning("Package WeTextProcessing not found!")
    logger.warning(
        "Run: conda install -c conda-forge pynini=2.1.5 && pip install WeTextProcessing",
    )

 NeMo-text-processing :: INFO     :: Creating ClassifyFst grammars.
[+0000 20241221 23:43:42] [INFO] NeMo-text-processing | tokenize_and_classify | Creating ClassifyFst grammars.
2024-12-21 23:44:17,049 WETEXT INFO found existing fst: /usr/local/lib/python3.10/dist-packages/tn/zh_tn_tagger.fst
[+0000 20241221 23:44:17] [INFO] wetext-zh_normalizer | processor | found existing fst: /usr/local/lib/python3.10/dist-packages/tn/zh_tn_tagger.fst
2024-12-21 23:44:17,054 WETEXT INFO                     /usr/local/lib/python3.10/dist-packages/tn/zh_tn_verbalizer.fst
[+0000 20241221 23:44:17] [INFO] wetext-zh_normalizer | processor |                     /usr/local/lib/python3.10/dist-packages/tn/zh_tn_verbalizer.fst
2024-12-21 23:44:17,057 WETEXT INFO skip building fst for zh_normalizer ...
[+0000 20241221 23:44:17] [INFO] wetext-zh_normalizer | processor | skip building fst for zh_normalizer ...


### Here are three choices for loading models,

#### 1. Load models from Hugging Face (recommend)

In [ ]:
# use force_redownload=True if the weights have been updated.
chat.load(source="huggingface")

#### 2. Load models from local directories 'asset' and 'config'

In [ ]:
chat.load()
# chat.load(source='local') same as above

#### 3. Load models from a custom path

In [ ]:
# write the model path into custom_path
chat.load(source="custom", custom_path="YOUR CUSTOM PATH")

### You can also unload models to save the memory

In [ ]:
chat.unload()

## Inference

### Batch infer

In [9]:
texts = [
    "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",
] * 3 + [
    "我觉得像我们这些写程序的人，他，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，就他们并不会轻易的开放给所有的人用。"
] * 3

wavs = chat.infer(texts)

text:   0%|          | 1/384(max) [00:01,  1.25s/it]We detected that you are passing `past_key_values` as a tuple of tuples. This is deprecated and will be removed in v4.47. Please convert your cache or use an appropriate `Cache` class (https://huggingface.co/docs/transformers/kv_cache#legacy-cache-format)
text:  29%|██▉       | 111/384(max) [00:04, 27.69it/s]
code:  44%|████▍     | 896/2048(max) [00:23, 38.55it/s]


In [14]:
Audio(wavs[1], rate=24_000, autoplay=True)

In [15]:
Audio(wavs[4], rate=24_000, autoplay=True)

### Custom params

In [21]:
spk = torch.load("/content/male_1185.pt")

params_infer_code = ChatTTS.Chat.InferCodeParams(
    prompt="[speed_5]",
    temperature=1,
    spk_emb = spk
)
params_refine_text = ChatTTS.Chat.RefineTextParams(
    prompt="[oral_0][laugh_0][break_6]",
    temperature=1,
    top_K = 1,
    top_P = 0.95
)

<ipython-input-21-8a8e995c9650>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  spk = torch.load("/content/male_1185.pt")
[+0000 20241222 00:08:57] [WARN] ChatTTS | norm | 

In [27]:
text = "为了揭示这些信息，《华尔街日报》收集了各州的报告，并将其与特斯拉提交给NHTSA的事故数据进行匹配，发现美国道路上出现的问题印证了人们长期以来对自动驾驶技术的担忧。在特斯拉提交的1000多起事故中，《华尔街日报》分析了其中的222起，发现44起涉及特斯拉在自动驾驶状态下突然转向，31起涉及特斯拉在自动驾驶状态下未能停车或对前方障碍物让行。在佛罗里达州奥兰多，一辆Model 3撞上了一辆停在路边处理故障车辆的警车。在德克萨斯州瓜达卢佩县，一辆Model 3冲过十字路口并驶离道路。这些未能停车的事故，就像导致Steven Hendrickson死亡的那起一样，在《华尔街日报》揭示的案例中造成了最严重的伤亡。事故发生后，Steven的妻子Janelle Hendrickson回忆道"

text_normalized = chat.normalizer(
    text,
    True,
    True,
    None,
)

text_normalized

[+0000 20241222 00:37:22] [WARN] ChatTTS | norm | found invalid characters: {'》', '《'}


'为了揭示这些信息，，华尔街日报，收集了各州的报告，并将其与特斯拉提交给NHTSA的事故数据进行匹配，发现美国道路上出现的问题印证了人们长期以来对自动驾驶技术的担忧。在特斯拉提交的一千多起事故中，，华尔街日报，分析了其中的二二二起，发现四十四起涉及特斯拉在自动驾驶状态下突然转向，三十一起涉及特斯拉在自动驾驶状态下未能停车或对前方障碍物让行。在佛罗里达州奥兰多，一辆Model 三撞上了一辆停在路边处理故障车辆的警车。在德克萨斯州瓜达卢佩县，一辆Model 三冲过十字路口并驶离道路。这些未能停车的事故，就像导致Steven Hendrickson死亡的那起一样，在，华尔街日报，揭示的案例中造成了最严重的伤亡。事故发生后，Steven的妻子Janelle Hendrickson回忆道'

In [24]:
wav = chat.infer(
    "为了揭示这些信息，《华尔街日报》收集了各州的报告，并将其与特斯拉提交给NHTSA的事故数据进行匹配，发现美国道路上出现的问题印证了人们长期以来对自动驾驶技术的担忧。在特斯拉提交的1000多起事故中，《华尔街日报》分析了其中的222起，发现44起涉及特斯拉在自动驾驶状态下突然转向，31起涉及特斯拉在自动驾驶状态下未能停车或对前方障碍物让行。在佛罗里达州奥兰多，一辆Model 3撞上了一辆停在路边处理故障车辆的警车。在德克萨斯州瓜达卢佩县，一辆Model 3冲过十字路口并驶离道路。这些未能停车的事故，就像导致Steven Hendrickson死亡的那起一样，在《华尔街日报》揭示的案例中造成了最严重的伤亡。事故发生后，Steven的妻子Janelle Hendrickson回忆道",
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)

Audio(wav[0], rate=24_000, autoplay=True)

[+0000 20241222 00:12:38] [WARN] ChatTTS | norm | found invalid characters: {'》', '《'}
text:  83%|████████▎ | 318/384(max) [00:07, 44.56it/s]
code:  74%|███████▍  | 1525/2048(max) [00:36, 42.30it/s]


### fix random speaker

In [ ]:
rand_spk = chat.sample_random_speaker()
print(rand_spk)  # save it for later timbre recovery

params_infer_code = ChatTTS.Chat.InferCodeParams(
    spk_emb=rand_spk,
)

wav = chat.infer(
    "四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。",
    params_infer_code=params_infer_code,
)

In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)

### Zero shot (simulate speaker)

In [ ]:
from ChatTTS.tools.audio import load_audio

spk_smp = chat.sample_audio_speaker(load_audio("sample.mp3", 24000))
print(spk_smp)  # save it in order to load the speaker without sample audio next time

params_infer_code = ChatTTS.Chat.InferCodeParams(
    spk_smp=spk_smp,
    txt_smp="与sample.mp3内容完全一致的文本转写。",
)

wav = chat.infer(
    "四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。",
    params_infer_code=params_infer_code,
)

In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)

### Two stage control

In [ ]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
refined_text = chat.infer(text, refine_text_only=True)
refined_text

In [ ]:
wav = chat.infer(refined_text, skip_refine_text=True)

In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)

## LLM Call

In [ ]:
from ChatTTS.tools.llm import ChatOpenAI

API_KEY = ""
client = ChatOpenAI(
    api_key=API_KEY, base_url="https://api.deepseek.com", model="deepseek-chat"
)

In [ ]:
user_question = "四川有哪些好吃的美食呢?"

In [ ]:
text = client.call(user_question, prompt_version="deepseek")
text

In [ ]:
text = client.call(text, prompt_version="deepseek_TN")
text

In [ ]:
wav = chat.infer(text)

In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)